In [2]:
import pandas as pd
import numpy as np
import json
import torch
import torch.nn as nn
from sentence_transformers import SentenceTransformer
from sklearn.preprocessing import StandardScaler, OrdinalEncoder

### Encode categorical variables and upscale to consistent size

In [64]:
# Import data
features= pd.read_csv("features.csv")
features = features.drop(columns=["Unnamed: 0"], axis= 1)
features.head()

track_id                 artists  \
0  5SuOikwiRyPMVoIQDJUgSV             Gen Hoshino   
1  4qPNDBW1i3p13qLCt0Ki3A            Ben Woodward   
2  1iJBSr7s7jYXzM8EGcbK5b  Ingrid Michaelson;ZAYN   
3  6lfxq3CG4xtTiEg7opyCyx            Kina Grannis   
4  5vjLSffimiIP26QG5WcN2K        Chord Overstreet   

                                          album_name  \
0                                             Comedy   
1                                   Ghost (Acoustic)   
2                                     To Begin Again   
3  Crazy Rich Asians (Original Motion Picture Sou...   
4                                            Hold On   

                   track_name  popularity  duration_ms  explicit  \
0                      Comedy          73       230666     False   
1            Ghost - Acoustic          55       149610     False   
2              To Begin Again          57       210826     False   
3  Can't Help Falling In Love          71       201933     False   
4                     Hold On          82       198853     False   

   danceability  energy  key  loudness  mode  speechiness  acousticness  \
0         0.676  0.4610    1    -6.746     0       0.1430        0.0322   
1         0.420  0.1660    1   -17.235     1       0.0763        0.9240   
2         0.438  0.3590    0    -9.734     1       0.0557        0.2100   
3         0.266  0.0596    0   -18.515     1       0.0363        0.9050   
4         0.618  0.4430    2    -9.681     1       0.0526        0.4690   

   instrumentalness  liveness  valence    tempo  time_signature track_genre  
0          0.000001    0.3580    0.715   87.917               4    acoustic  
1          0.000006    0.1010    0.267   77.489               4    acoustic  
2          0.000000    0.1170    0.120   76.332               4    acoustic  
3          0.000071    0.1320    0.143  181.740               3    acoustic  
4          0.000000    0.0829    0.167  119.949               4    acoustic

In [4]:
# Data overview
features.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 114000 entries, 0 to 113999
Data columns (total 20 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   track_id          114000 non-null  object 
 1   artists           113999 non-null  object 
 2   album_name        113999 non-null  object 
 3   track_name        113999 non-null  object 
 4   popularity        114000 non-null  int64  
 5   duration_ms       114000 non-null  int64  
 6   explicit          114000 non-null  bool   
 7   danceability      114000 non-null  float64
 8   energy            114000 non-null  float64
 9   key               114000 non-null  int64  
 10  loudness          114000 non-null  float64
 11  mode              114000 non-null  int64  
 12  speechiness       114000 non-null  float64
 13  acousticness      114000 non-null  float64
 14  instrumentalness  114000 non-null  float64
 15  liveness          114000 non-null  float64
 16  valence           11

In [5]:
features.describe()

popularity   duration_ms   danceability         energy  \
count  114000.000000  1.140000e+05  114000.000000  114000.000000   
mean       33.238535  2.280292e+05       0.566800       0.641383   
std        22.305078  1.072977e+05       0.173542       0.251529   
min         0.000000  0.000000e+00       0.000000       0.000000   
25%        17.000000  1.740660e+05       0.456000       0.472000   
50%        35.000000  2.129060e+05       0.580000       0.685000   
75%        50.000000  2.615060e+05       0.695000       0.854000   
max       100.000000  5.237295e+06       0.985000       1.000000   

                 key       loudness           mode    speechiness  \
count  114000.000000  114000.000000  114000.000000  114000.000000   
mean        5.309140      -8.258960       0.637553       0.084652   
std         3.559987       5.029337       0.480709       0.105732   
min         0.000000     -49.531000       0.000000       0.000000   
25%         2.000000     -10.013000       0.000000       0.035900   
50%         5.000000      -7.004000       1.000000       0.048900   
75%         8.000000      -5.003000       1.000000       0.084500   
max        11.000000       4.532000       1.000000       0.965000   

        acousticness  instrumentalness       liveness        valence  \
count  114000.000000     114000.000000  114000.000000  114000.000000   
mean        0.314910          0.156050       0.213553       0.474068   
std         0.332523          0.309555       0.190378       0.259261   
min         0.000000          0.000000       0.000000       0.000000   
25%         0.016900          0.000000       0.098000       0.260000   
50%         0.169000          0.000042       0.132000       0.464000   
75%         0.598000          0.049000       0.273000       0.683000   
max         0.996000          1.000000       1.000000       0.995000   

               tempo  time_signature  
count  114000.000000   114000.000000  
mean      122.147837        3.904035  
std        29.978197        0.432621  
min         0.000000        0.000000  
25%        99.218750        4.000000  
50%       122.017000        4.000000  
75%       140.071000        4.000000  
max       243.372000        5.000000

In [65]:
# Remove duplicates
features = features.drop_duplicates()
# Handle missing data
features.isna().sum()
features= features.dropna()

In [66]:
# Get encoded genre descriptions
with open("encoded_genre_descriptions.json") as f:
    content= json.load(f)

In [ ]:
# Categorical data encoding

# Replace genres with encoded descriptions
features["track_genre"] = features["track_genre"].map(content)

# Sentence transformer
st = SentenceTransformer("all-MiniLM-L6-v2")
# Encode text data
features["album_name"] = features["album_name"].apply(st.encode)
features["track_name"] = features["track_name"].apply(st.encode)

# Ordinal encoder
oe= OrdinalEncoder()
# Ordinal encode artists as it doesnt hold semantic meaning
features["artists"] = oe.fit_transform(features[["artists"]])

features

In [86]:
features_embeddings= features.copy()
# Compute mean for genre embeddings while keeping all else unchanged
grouping = features_embeddings.groupby("track_id", as_index=False)["track_genre"].agg(lambda x: np.mean(np.stack((x)), axis=0))
# Drop duplicates, keeping the first occurrence of all other features
features_embeddings = features_embeddings.drop(columns=["track_genre"]).drop_duplicates(subset=["track_id"])
features_embeddings = features_embeddings.merge(grouping, on="track_id", how="left")

In [ ]:
# Previous cell took 159m save to pkl
features_embeddings.to_pickle("features_preprocessed.pkl")

In [22]:
features_embeddings= pd.read_pickle("features_preprocessed.pkl")

In [87]:
# Scalar normaliziation
scaler= StandardScaler()

# Quickly change explicit to float
features_embeddings["explicit"] = features_embeddings["explicit"] * 1.0

scalars= [col for col in features_embeddings.columns if  features_embeddings[col].dtype in ["int64", "float64"]]
features_embeddings[scalars] = scaler.fit_transform(features_embeddings[scalars])

In [89]:
# Normalize embeddings

# Function to L2 normalize embeddings
def l2_normalize_1d(array):
    norm = np.linalg.norm(array)
    return array / norm if norm != 0 else array

embeddings= ["track_name", "album_name"]
# Normalize each embedding column
for col in embeddings:
    features_embeddings[col] = features_embeddings[col].apply(l2_normalize_1d)

features_embeddings

track_id   artists  \
0      5SuOikwiRyPMVoIQDJUgSV -0.595234   
1      4qPNDBW1i3p13qLCt0Ki3A -1.376509   
2      1iJBSr7s7jYXzM8EGcbK5b -0.369802   
3      6lfxq3CG4xtTiEg7opyCyx -0.099947   
4      5vjLSffimiIP26QG5WcN2K -1.159034   
...                       ...       ...   
89735  2C3TZjDRiAzdyViavDJ217  0.745090   
89736  1hIz5L4IB9hN3WRYPOCGPw  0.745090   
89737  6x8ZfSoqDjuNa5SVP5QjvX -1.192517   
89738  2e6sXL2bYv4bSz6VTdnfLs  0.308371   
89739  2hETkH7cOfqmz3LqZDHZf5 -1.192517   

                                              album_name  \
0      [-0.042611223, -0.046201088, -0.03457106, 0.01...   
1      [-0.055657774, -0.019521242, 0.023629805, -0.0...   
2      [-0.0340062, -0.054437377, 0.014670651, 0.0601...   
3      [-0.04945588, 0.02640154, -0.02629091, 0.04236...   
4      [-0.09101045, -0.057857774, -0.011362545, -0.0...   
...                                                  ...   
89735  [0.013029114, -0.0064732456, 0.11790641, 0.005...   
89736  [0.013029114, -0.0064732456, 0.11790641, 0.005...   
89737  [-0.14179662, 0.04931275, 0.017334942, -0.0407...   
89738  [0.032583725, 0.052094545, 0.05051703, -0.0473...   
89739  [-0.0033045784, 0.08042111, -0.03275188, -0.00...   

                                              track_name  popularity  \
0      [-0.042611223, -0.046201088, -0.03457106, 0.01...    1.933925   
1      [-0.072181344, 0.011208587, 0.03520768, -0.047...    1.059312   
2      [-0.0340062, -0.054437377, 0.014670651, 0.0601...    1.156491   
3      [-0.051752593, -0.032192286, 0.088695966, 0.03...    1.836746   
4      [-0.09101045, -0.057857774, -0.011362545, -0.0...    2.371232   
...                                                  ...         ...   
89735  [-0.0065607643, 0.09955642, -0.031772323, 0.03...   -0.592735   
89736  [-0.014128448, 0.021833342, 0.034011472, 0.091...   -0.544146   
89737  [-0.0033045784, 0.08042111, -0.03275188, -0.00...   -0.544146   
89738  [-0.11017303, 0.068362534, 0.00659094, 0.03007...    0.379057   
89739  [-0.02734906, -0.0066746073, -0.06734158, -0.0...   -0.544146   

       duration_ms  explicit  danceability    energy       key  loudness  \
0         0.013472 -0.306447      0.644253 -0.675975 -1.203275  0.335727   
1        -0.704186 -0.306447     -0.804604 -1.825602 -1.203275 -1.673087   
2        -0.162188 -0.306447     -0.702731 -1.073473 -1.484183 -0.236524   
3        -0.240925 -0.306447     -1.676182 -2.240247 -1.484183 -1.918228   
4        -0.268195 -0.306447      0.315996 -0.746122 -0.922368 -0.226373   
...            ...       ...           ...       ...       ...       ...   
89735     1.379914 -0.306447     -2.208184 -1.556706 -0.079646 -1.511831   
89736     1.379923 -0.306447     -2.196865 -2.016557 -1.484183 -1.880499   
89737     0.374710 -0.306447      0.378251 -1.190384 -1.484183 -0.458874   
89738     0.484736 -0.306447      0.140548 -0.500608  0.482169 -0.457725   
89739     0.112281 -0.306447     -0.204687 -0.574652 -1.203275 -0.326536   

           mode  speechiness  acousticness  instrumentalness  liveness  \
0     -1.324621     0.490458     -0.875166         -0.535482  0.723656   
1      0.754933    -0.098364      1.760810         -0.535468 -0.595078   
2      0.754933    -0.280219     -0.349626         -0.535485 -0.512978   
3      0.754933    -0.451480      1.704650         -0.535266 -0.436009   
4      0.754933    -0.307585      0.415925         -0.535485 -0.687954   
...         ...          ...           ...               ...       ...   
89735  0.754933    -0.399395      0.921365          2.330062 -0.670508   
89736 -1.324621    -0.417934      1.967716          2.478280 -0.574553   
89737 -1.324621    -0.401161      1.592330         -0.535485 -0.682823   
89738  0.754933    -0.509744      0.155815         -0.535485  0.272105   
89739 -1.324621    -0.131910      1.042553         -0.535485 -0.655114   

        valence     tempo  time_signature  \
0      0.934047 -1.133599        0.226216   
1     -0.770269 -1.479843 

In [90]:
# Upscale scalars to match embeddings because RNN needs consistent shape

# Multi-layer perceptron 
class ScalarUpscaler(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(ScalarUpscaler, self).__init__()
        self.mlp = nn.Sequential(
            nn.Linear(input_dim, 128),
            nn.ReLU(),
            nn.Linear(128, output_dim)
        )
    
    def forward(self, x):
        return self.mlp(x)

# Initialize the ScalarUpscaler model
scalar_upscaler = ScalarUpscaler(input_dim=1, output_dim=384)


# Upscale each scalar column
for col in scalars:
    upscaled_tensor = scalar_upscaler(torch.tensor(features_embeddings[col].values, dtype=torch.float32).unsqueeze(1)) # Flatten
    features_embeddings[f"{col}_upscaled"] = list(upscaled_tensor.detach().numpy())  # Detatch from grad and convert to NumPy
    features_embeddings = features_embeddings.drop(col, axis=1)

In [91]:
features_embeddings

track_id  \
0      5SuOikwiRyPMVoIQDJUgSV   
1      4qPNDBW1i3p13qLCt0Ki3A   
2      1iJBSr7s7jYXzM8EGcbK5b   
3      6lfxq3CG4xtTiEg7opyCyx   
4      5vjLSffimiIP26QG5WcN2K   
...                       ...   
89735  2C3TZjDRiAzdyViavDJ217   
89736  1hIz5L4IB9hN3WRYPOCGPw   
89737  6x8ZfSoqDjuNa5SVP5QjvX   
89738  2e6sXL2bYv4bSz6VTdnfLs   
89739  2hETkH7cOfqmz3LqZDHZf5   

                                              album_name  \
0      [-0.042611223, -0.046201088, -0.03457106, 0.01...   
1      [-0.055657774, -0.019521242, 0.023629805, -0.0...   
2      [-0.0340062, -0.054437377, 0.014670651, 0.0601...   
3      [-0.04945588, 0.02640154, -0.02629091, 0.04236...   
4      [-0.09101045, -0.057857774, -0.011362545, -0.0...   
...                                                  ...   
89735  [0.013029114, -0.0064732456, 0.11790641, 0.005...   
89736  [0.013029114, -0.0064732456, 0.11790641, 0.005...   
89737  [-0.14179662, 0.04931275, 0.017334942, -0.0407...   
89738  [0.032583725, 0.052094545, 0.05051703, -0.0473...   
89739  [-0.0033045784, 0.08042111, -0.03275188, -0.00...   

                                              track_name  \
0      [-0.042611223, -0.046201088, -0.03457106, 0.01...   
1      [-0.072181344, 0.011208587, 0.03520768, -0.047...   
2      [-0.0340062, -0.054437377, 0.014670651, 0.0601...   
3      [-0.051752593, -0.032192286, 0.088695966, 0.03...   
4      [-0.09101045, -0.057857774, -0.011362545, -0.0...   
...                                                  ...   
89735  [-0.0065607643, 0.09955642, -0.031772323, 0.03...   
89736  [-0.014128448, 0.021833342, 0.034011472, 0.091...   
89737  [-0.0033045784, 0.08042111, -0.03275188, -0.00...   
89738  [-0.11017303, 0.068362534, 0.00659094, 0.03007...   
89739  [-0.02734906, -0.0066746073, -0.06734158, -0.0...   

                                             track_genre  \
0      [0.04281982313841581, -0.0413171318359673, 0.0...   
1      [0.07256904989480972, -0.014707725495100021, 0...   
2      [0.09977447986602783, -0.0242838766425848, 0.0...   
3      [0.09977447986602783, -0.0242838766425848, 0.0...   
4      [0.09977447986602783, -0.0242838766425848, 0.0...   
...                                                  ...   
89735  [0.0747806504368782, 0.006442745216190815, -0....   
89736  [0.0747806504368782, 0.006442745216190815, -0....   
89737  [0.0747806504368782, 0.006442745216190815, -0....   
89738  [0.0747806504368782, 0.006442745216190815, -0....   
89739  [0.0747806504368782, 0.006442745216190815, -0....   

                                        artists_upscaled  \
0      [0.22623691, -0.2630899, 0.28008905, 0.3336281...   
1      [0.5738303, -0.37058035, 0.028592411, 0.365585...   
2      [0.1852988, -0.24752226, 0.31499597, 0.2979095...   
3      [0.14099935, -0.24439871, 0.3568103, 0.2557095...   
4      [0.44504857, -0.32536805, 0.09222077, 0.381935...   
...                                                  ...   
89735  [0.14431867, -0.10190673, 0.52013546, 0.084200...   
89736  [0.14431867, -0.10190673, 0.52013546, 0.084200...   
89737  [0.46372247, -0.33253726, 0.08140024, 0.379649...   
89738  [0.13270143, -0.2018072, 0.41665906, 0.1590969...   
89739  [0.46372247, -0.33253726, 0.08140024, 0.379649...   

                                     popularity_upscaled  \
0      [0.23569924, 0.07754627, 0.9953241, -0.1993762...   
1      [0.14794555, 0.008012899, 0.63925403, 0.051020...   
2      [0.14957899, 0.031931207, 0.6845803, 0.0294982...   
3      [0.22563717, 0.07963715, 0.95666605, -0.171957...   
4      [0.29041368, 0.063367724, 1.149627, -0.321417,...   
...                                                  ...   
89735  [0.22563553, -0.26293394, 0.28080302, 0.333378...   
89736  [0.21448034, -0.25858068, 0.29267162, 0.330180...   
89737  [0.21448034, -0.25858068, 0.29267162, 0.330180...   
89738  [0.13932729, -0.18561158, 0.42638168, 0.146134...   
89739  [0.21448034, -0.25858068, 0.29267162, 0.330180...   

                   

In [ ]:
for col in features_embeddings.columns:
    if col == "track_id":
        continue
    for row in features_embeddings[col]:
        if len(row) != 384:
            print("length mismatch")

In [117]:
# Save to pkl
features_embeddings.to_pickle("features_preprocessed.pkl")